In [15]:
import numpy as np
import matplotlib.pyplot as plt
from scipy.integrate import odeint, solve_ivp
import math
import pypower
from pypower.api import case9, ppoption, runpf, printpf
from copy import deepcopy

import pandas as pd


def dx_dt(x, t, fault_time, Y, V0, Pm, M):
    ps = 0

    for k in range(len(fault_time)):
        if t > fault_time[k]:
            ps = k + 1

    if t > 1:
        a = 0

    Ybus = Y[ps]
    Vg = V0 * np.exp(1j * x[0:3])
    Ibus = np.matmul(Ybus, Vg)
    S = np.conj(Ibus) * Vg
    Pe = np.real(S)
    dx = x[3:6]
    return np.hstack([dx, (Pm - Pe) / M])


def CalYbus(branch):
    Nbus = int(max([max(branch[:, 0]), max(branch[:, 1])]))
    Nbranch = len(branch[:, 0])
    Ybus = np.zeros([Nbus, Nbus])
    Ybus = np.complex_(Ybus)
    for k in range(Nbranch):
        N1 = int(branch[k, 0] - 1)
        N2 = int(branch[k, 1] - 1)
        YY = 1/(branch[k, 2]+1j*branch[k, 3])
        tap = branch[k, 8]
        if tap == 0:
            tap = 1

        tap = 1/tap
        Ybus[N1, N1] = Ybus[N1, N1] + tap * tap * YY + 1j * branch[k, 4]
        Ybus[N2, N2] = Ybus[N2, N2] + YY + 1j * branch[k, 4]
        Ybus[N1, N2] = Ybus[N1, N2] - tap * YY
        Ybus[N2, N1] = Ybus[N2, N1] - tap * YY
    return Ybus


def Ybus_aumentada(system): 
    result = pypower.api.runpf(system)[0]
    Nbus = int(max([max(system['branch'][:, 0]), max(system['branch'][:, 1])]))
    NG   = system['gen'][:, 0]
    Ngen = len(NG)
    Nload = system['bus'][[4, 6, 8], 0]
    NumC = len(Nload)
    YbusB = CalYbus(system['branch'])
    Ybus = np.zeros([Nbus + Ngen, Nbus + Ngen])
    Ybus = np.complex_(Ybus)
    Ybus[0:Nbus, 0:Nbus] = YbusB
    Vn = np.zeros([3, 1])
    Vn = np.complex_(Vn)
    for k in range(Ngen):
        n = int(NG[k]) - 1
        kk = k + Nbus
        xd = system['gen'][k, 21]
        yd = 1/(1j*xd)
        Ybus[n, n] = Ybus[n, n] + yd
        Ybus[kk, kk] = Ybus[kk, kk] + yd
        Ybus[kk, n] = Ybus[kk, n] - yd
        Ybus[n, kk] = Ybus[n, kk] - yd
        # generator internal voltage
        Vbus = result['bus'][n, 7] * (np.cos(result['bus'][n, 7] * math.pi / 180) + 1j * np.sin(result['bus'][n, 8] * math.pi/180))
        I = np.conj((result['gen'][n, 1] + 1j * result['gen'][n, 2]) / 100 / Vbus)
        Vn[k, 0] = Vbus + 1j*xd*I

    # convert loads to impedances and include them in the Ybus
    for k in range(NumC):
        n = int(Nload[k]) - 1
        S = (result['bus'][n, 2] + 1j * result['bus'][n, 3]) / 100
        Vbus = result['bus'][n, 7] * (np.cos(result['bus'][n, 7] * math.pi / 180) + 1j * np.sin(result['bus'][n, 7] * math.pi / 180))
        V = abs(Vbus)
        Y = np.conj(S/(V*V))
        Ybus[n, n] = Ybus[n, n] + Y
    return Ybus, Vn


def  Ybus_reduction(Ybus, NN, NR):
    Yg = Ybus[NN:NN+NR, NN:NN+NR]
    Yb = Ybus[NN:NN+NR, 0:NN]
    Yc = Ybus[0:NN, NN:NN+NR]
    Ye = Ybus[0:NN, 0:NN]
    Ybusr = Yg - Yb@np.linalg.inv(Ye)@Yc
    return Ybusr


def fault(Ybus, fault_branch):
    bus = np.arange(0, 12, 1)
    if fault_branch == 1:
        fault_bus = 3
    if fault_branch == 4:
        fault_bus = 5
    if fault_branch == 5:
        fault_bus = 7
    Ybus_fault = np.delete(Ybus, fault_bus, 0)
    Ybus_fault = np.delete(Ybus_fault, fault_bus, 1)
    return Ybus_fault


def post_fault_Ybus(system, fault_branch, Ybus):
    Ybusx =Ybus
    N1 = int(system['branch'][fault_branch,0]-1)
    N2 = int(system['branch'][fault_branch,1]-1)
    YY = 1/(system['branch'][fault_branch,2]+1j*system['branch'][fault_branch,3])
    bkm = system['branch'][fault_branch,4]
    tap = 1.0
    if tap==0:
        tap = 1.0
    tap = 1/tap
    Ybusx[N1,N1] = Ybusx[N1,N1] - tap*tap*YY - 1j*bkm
    Ybusx[N2,N2] = Ybusx[N2,N2] - YY         - 1j*bkm
    Ybusx[N1,N2] = Ybusx[N1,N2] + tap*YY
    Ybusx[N2,N1] = Ybusx[N2,N1] + tap*YY
    return Ybusx


def post_fault(system, fault_branch):
    case_new = deepcopy(system)
    branch_new = np.delete(case_new['branch'], fault_branch, axis=0)
    case_new['branch'] = branch_new
    return case_new 


def cal_stability(power_system, fault_branch):
    system = pypower.api.runpf(power_system)[0]
    #Inertia values for generator
    M = 2 * np.array([23.64, 6.80, 3.01]) / (2 * math.pi * 50) 
    #time(s):[short_circuit, open_time]
    fault_time = [0.1, 0.6] #play around with this to see when the stability improves
    Pm = system['gen'][:, 1] / 100
    t = np.linspace(0, 10, 1001)

    Ybus, Vn = Ybus_aumentada(system)
    Y_nofault = Ybus_reduction(Ybus, 9, 3)

    Ybus_fault = fault(Ybus, fault_branch)
    Y_fault = Ybus_reduction(Ybus_fault, 8, 3)

    system_post_fault = post_fault(system, fault_branch)
    Ybus_post_fault, _ = Ybus_aumentada(system_post_fault)
    Y_post_fault = Ybus_reduction(Ybus_post_fault, 9, 3)


    Y = {0: Y_nofault,
         1: Y_fault,
         2: Y_post_fault}
    x0 = np.hstack([np.transpose(np.angle(Vn)), np.mat([0, 0, 0])]).tolist()[0]
    V0 = np.transpose(np.abs(Vn)).tolist()[0]

    x = odeint(dx_dt, x0, t, args=(fault_time, Y, V0, Pm, M))

    MT = sum(M)
    xcoi = np.zeros([len(x), 3]) #rotor angle values
    d_max = np.zeros(len(x))
    for k in range(len(x)):
        d = sum(x[k, 0:3] * M) / MT
        # w = sum(x[k, 3:6] * M) / MT
        xcoi[k, :] = x[k, 0:3] - [d, d, d]
        d_max[k] = max(xcoi[k, :]) - min(xcoi[k, :])

    return xcoi, max(d_max)*180/math.pi


#load the excel as pandas dataframe
bus_loads_imag = pd.read_excel('IEEE9bus_loads.xlsx', header=None, sheet_name='loads_imag')
bus_loads_imag = bus_loads_imag*100
bus_loads_imag = round(bus_loads_imag,2)

bus_loads_real = pd.read_excel('IEEE9bus_loads.xlsx', header=None, sheet_name='loads_real')
bus_loads_real = bus_loads_real*100
bus_loads_real = round(bus_loads_real,2)

d_max = [] #if d_mx is >180 its unstable
xcoi = []

for row in range(1000): 
#This simulation is for a single load. Loop through all the loads to calculate the stability index
    power_system = pypower.api.runpf(pypower.api.case9())[0]
    #Active power on load buses
    power_system['bus'][[4, 6, 8], 2] = [56.28, 43.16, 127.68] #replace these with the page 1 values 
    #Reactive power on load buses
    power_system['bus'][[4, 6, 8], 3] = [27.34, 33.77, 45.25] #replace these with the page 2 values

    fault_branch = 5 #is this constant? #try changing to see what happens #focus on one fault usually 

    xcoi_temp, d_max_temp = cal_stability(power_system, fault_branch)
    d_max.append(d_max_temp)
    xcoi.append(xcoi)

print(d_max)




PYPOWER Version 5.1.4, 27-June-2018 -- AC Power Flow (Newton)


Newton's method power flow converged in 4 iterations.

Converged in 0.02 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    318.0              24.8
Loads              3     Load                   315.0             115.0
  Fixed            3       Fixed                315.0             115.0
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)         2.98             41.97
Transformers       0     Branch 

[36787.03943338419]


In [16]:
d_max

[36787.03943338419]

In [26]:
xcoi

[[...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],
 [...],


In [27]:
stable_pnts = ([x for x in d_max if x<=180]) #stable points

In [28]:
indexes = []
for j in stable_pnts:
    indexes.append(d_max.index(j))

In [29]:
len(indexes)

549

In [14]:
stable_bus_loads_real = []
for i in indexes:
    stable_bus_loads_real.append([bus_loads_real[0][i], bus_loads_real[1][i], bus_loads_real[2][i]])

stable_bus_loads_real

549

In [16]:
stable_bus_loads_real = pd.DataFrame(stable_bus_loads_real)

In [17]:
stable_bus_loads_real

0       1       2
0     94.44  139.39  126.20
1     98.12  147.92  165.88
2     87.79  138.81  112.39
3    108.61  138.05   92.41
4    103.48  127.66  169.91
..      ...     ...     ...
544  123.45  123.08  145.18
545   64.24  108.04  162.63
546  132.70   73.26  167.36
547  127.30   81.87  128.36
548   69.49   98.46  132.15

[549 rows x 3 columns]

In [18]:
stable_bus_loads_imag = []
for i in indexes:
    stable_bus_loads_imag.append([bus_loads_imag[0][i], bus_loads_imag[1][i], bus_loads_imag[2][i]])

stable_bus_loads_imag = pd.DataFrame(stable_bus_loads_imag)

In [19]:
stable_bus_loads_imag

0      1      2
0    26.18  34.31  56.51
1    25.03  34.60  52.66
2    28.79  35.65  49.67
3    24.54  30.66  57.42
4    32.86  31.42  52.64
..     ...    ...    ...
544  26.12  37.34  55.18
545  25.47  40.88  56.49
546  30.40  37.64  44.41
547  26.83  32.83  47.05
548  24.32  41.66  50.44

[549 rows x 3 columns]

In [21]:
with pd.ExcelWriter('Stable_Loads.xlsx') as writer:  
    stable_bus_loads_real.to_excel(writer, sheet_name='loads_real', header=False, index=False)
    stable_bus_loads_imag.to_excel(writer, sheet_name='loads_imag', header=False, index=False)

In [23]:
unstable_bus_loads_real = bus_loads_real.drop(indexes)
unstable_bus_loads_imag = bus_loads_imag.drop(indexes)

In [24]:
with pd.ExcelWriter('Unstable_Loads.xlsx') as writer:  
    unstable_bus_loads_real.to_excel(writer, sheet_name='loads_real', header=False, index=False)
    unstable_bus_loads_imag.to_excel(writer, sheet_name='loads_imag', header=False, index=False)

#  TEST UNSTABLE POINTS

In [24]:
unstable_bus_loads_gen1 = pd.read_excel('Unstable_Points_Gen.xlsx', sheet_name='gen1')
unstable_bus_loads_gen2 = pd.read_excel('Unstable_Points_Gen.xlsx', sheet_name='gen2')
unstable_bus_loads_gen3 = pd.read_excel('Unstable_Points_Gen.xlsx', sheet_name='gen3')
unstable_bus_loads_gen3

Rotor Angle  Active Power  Voltage Mag  stable  Predicted Active Power
0       3.043900        117.59     0.971823       0              127.902103
1       5.085611         92.53     0.971354       0              808.684201
2       2.924719        157.99     0.954855       0              144.250573
3       3.083992        120.44     0.970884       0              127.681799
4       3.138733        111.82     0.976770       0              121.928824
..           ...           ...          ...     ...                     ...
446     3.148503        132.53     0.966038       0              130.845460
447     3.875790         67.14     0.981787       0              172.707052
448     2.899976        128.02     0.956250       0              144.252775
449     2.996065         65.18     0.964546       0              134.841612
450     3.090637         79.92     0.975904       0              123.505493

[451 rows x 5 columns]

In [21]:
unstable_bus_loads_imag = pd.read_excel('Unstable_Loads.xlsx', header=None, sheet_name='loads_imag')
unstable_bus_loads_imag

0      1      2
0    32.18  36.54  42.93
1    32.16  29.08  49.18
2    34.25  38.35  51.24
3    27.34  33.77  45.25
4    25.95  40.77  40.47
..     ...    ...    ...
446  24.98  35.43  49.42
447  34.02  40.25  41.24
448  31.61  28.54  58.28
449  24.77  41.20  58.39
450  31.16  37.96  44.35

[451 rows x 3 columns]

In [27]:
unstable_pred_AP = []

for e in range (len(unstable_bus_loads_gen1['Predicted Active Power'])):
    unstable_pred_AP.append([unstable_bus_loads_gen1['Predicted Active Power'][e], unstable_bus_loads_gen2['Predicted Active Power'][e], unstable_bus_loads_gen3['Predicted Active Power'][e]])

unstable_pred_AP


[[81.89256337148129, 74.69237265114376, 127.9021027327664],
 [-81343.04520493138, 33108.125222412, 808.6842009514244],
 [80.58026110989033, 45.51287316517815, 144.2505730658801],
 [56.27541450274168, 43.16408674785058, 127.6817987359547],
 [45.51674336058079, 80.61853688405486, 121.9288235546482],
 [84.3877135799545, 71.82777809552468, 133.7019702836871],
 [-68150.0078905164, 33304.87773546769, 1004.283925402188],
 [79.74004524064242, 79.41294229073597, 128.2841353820365],
 [76.93807990712105, 55.21295108736618, 134.2868334517636],
 [64.8790319175738, 86.06602803552929, 124.0237228520872],
 [87.67772726950227, 82.99428513087574, 134.5756076695108],
 [67.28454643351017, 64.68470034722182, 132.9482451465826],
 [73.72102029857217, 85.96561649211313, 138.6374699473599],
 [109.9184243143815, 57.26426439211687, 138.1087617051617],
 [82.9252491430658, 76.65040175952132, 139.2439473605404],
 [66.46544478324233, 87.48476123871902, 131.9684238036731],
 [62.50225173545061, 43.45288189107455, 122.

In [34]:
unstable_bus_loads_imag[1][1]

29.08

In [35]:
d_max = [] #if d_mx is >180 its unstable
xcoi = []

for row in range(451): 
#This simulation is for a single load. Loop through all the loads to calculate the stability index
    power_system = pypower.api.runpf(pypower.api.case9())[0]
    #Active power on load buses
    power_system['bus'][[4, 6, 8], 2] = [unstable_pred_AP[row][0], unstable_pred_AP[row][1], unstable_pred_AP[row][2]] #replace these with the page 1 values 
    #Reactive power on load buses
    power_system['bus'][[4, 6, 8], 3] = [unstable_bus_loads_imag[0][row], unstable_bus_loads_imag[1][row], unstable_bus_loads_imag[2][row]] #replace these with the page 2 values

    fault_branch = 5 #is this constant? #try changing to see what happens #focus on one fault usually 

    xcoi_temp, d_max_temp = cal_stability(power_system, fault_branch)
    d_max.append(d_max_temp)
    xcoi.append(xcoi)

PYPOWER Version 5.1.4, 27-June-2018 -- AC Power Flow (Newton)


Newton's method power flow converged in 4 iterations.

Converged in 0.03 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    318.0              24.8
Loads              3     Load                   315.0             115.0
  Fixed            3       Fixed                315.0             115.0
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)         2.98             41.97
Transformers       0     Branch 


Newton's method power flow converged in 4 iterations.

Converged in 0.02 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    318.0              24.8
Loads              3     Load                   315.0             115.0
  Fixed            3       Fixed                315.0             115.0
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)         2.98             41.97
Transformers       0     Branch Charging (inj)     -              132.2
Inter-ties         0   


Did not converge (0.05 seconds)

|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    -48.7           52747.8
Loads              3     Load                 -47426.2             110.4
  Fixed            3       Fixed              -47426.2             110.4
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           8     Losses (I^2 * Z)     787278.87          5891138.64
Transformers       0     Branch Charging (inj)     -            51562.8
Inter-ties         0     Total Inter-tie Flow     0.0             


Newton's method power flow converged in 3 iterations.

Converged in 0.02 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    230.3               1.1
Loads              3     Load                   227.1             106.4
  Fixed            3       Fixed                227.1             106.4
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)         3.23             28.31
Transformers       0     Branch Charging (inj)     -              133.6
Inter-ties         0   


Newton's method power flow converged in 4 iterations.

Converged in 0.03 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    318.0              24.8
Loads              3     Load                   315.0             115.0
  Fixed            3       Fixed                315.0             115.0
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)         2.98             41.97
Transformers       0     Branch Charging (inj)     -              132.2
Inter-ties         0   

...


Newton's method power did not converge in 10 iterations.

Did not converge (0.06 seconds)

|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)  -1074.7           54413.1
Loads              3     Load                 -30089.0             114.8
  Fixed            3       Fixed              -30089.0             114.8
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)     340851.02          4164268.57
Transformers       0     Branch Charging (inj)     -            24540.6
Inter-ti

PYPOWER Version 5.1.4, 27-June-2018 -- AC Power Flow (Newton)


Newton's method power flow converged in 4 iterations.

Converged in 0.02 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    318.0              24.8
Loads              3     Load                   315.0             115.0
  Fixed            3       Fixed                315.0             115.0
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)         2.98             41.97
Transformers       0     Branch 


Newton's method power flow converged in 3 iterations.

Converged in 0.02 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    297.6              46.5
Loads              3     Load                   293.4             115.5
  Fixed            3       Fixed                293.4             115.5
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           8     Losses (I^2 * Z)         4.27             46.56
Transformers       0     Branch Charging (inj)     -              115.6
Inter-ties         0   

PYPOWER Version 5.1.4, 27-June-2018 -- AC Power Flow (Newton)


Newton's method power flow converged in 4 iterations.

Converged in 0.04 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    318.0              24.8
Loads              3     Load                   315.0             115.0
  Fixed            3       Fixed                315.0             115.0
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)         2.98             41.97
Transformers       0     Branch 

PYPOWER Version 5.1.4, 27-June-2018 -- AC Power Flow (Newton)


Newton's method power flow converged in 4 iterations.

Converged in 0.03 seconds
|     System Summary                                                           |

How many?                How much?              P (MW)            Q (MVAr)
---------------------    -------------------  -------------  -----------------
Buses              9     Total Gen Capacity     820.0        -900.0 to 900.0
Generators         3     On-line Capacity       820.0        -900.0 to 900.0
Committed Gens     3     Generation (actual)    318.0              24.8
Loads              3     Load                   315.0             115.0
  Fixed            3       Fixed                315.0             115.0
  Dispatchable     0       Dispatchable           0.0 of 0.0        0.0
Shunts             0     Shunt (inj)              0.0               0.0
Branches           9     Losses (I^2 * Z)         2.98             41.97
Transformers       0     Branch 

In [38]:
len(d_max)

451

In [37]:
stable_pnts = ([x for x in d_max if x<=180]) #stable points

In [39]:
len(stable_pnts)

139